## We investigate the backward gradient...




In [10]:
from function_regression.data_regression_experiment import sample_random_arrays
from function_regression.data_regression_experiment import run_data_experiment
from function_regression.functions.gaussian_mixture_function import GaussianMixtureFunction
from function_regression.models.urbf_mlp import URBFMLP
from function_regression.sgd_trainer import SGDTrainer
from function_regression.datasets.pmlb_dataset import PMLBDataset
import numpy as np
import exputils as eu
import function_regression

config = eu.AttrDict(
    # random seed for the repetition
    seed = 1234 + 2,

    model = eu.AttrDict(
        cls=function_regression.models.URBFMLP,
        hidden_features=[16,16,32,16,8],
        use_urbf=True,
        ranges=(0,100),
        use_split_merge=False,
        split_merge_temperature=0.1,
        use_back_tray=True,
        back_tray_ratio = 0.5
    ),

    dataset = eu.AttrDict(
        cls=function_regression.datasets.PMLBDataset,
        name="663_rabe_266"
        ),
    
    trainer = eu.AttrDict(
        cls=function_regression.SGDTrainer,
        learning_rate=0.1,
        urbf_learning_rate=1,
        n_epochs=1000,
        batch_size=64
    ),
)


# define the default configuration
default_config = eu.AttrDict(
    model = eu.AttrDict(cls=URBFMLP),
    function = eu.AttrDict(
        cls=GaussianMixtureFunction,
        in_features=2,
        difficulty=2,
        ranges=[(-5,5),(-5,5)],),
    trainer = eu.AttrDict(cls=SGDTrainer),
    seed = 123,
    test_split_size = 0.2,
    val_split_size = 0.2,
    log_to_tensorboard = True,
)

# set the config based on the default config, given config, and the given function arguments
config = eu.combine_dicts( config, default_config)
dataset = eu.misc.create_object_from_config(config.dataset)

dataset.plot()

fetching: 663_rabe_266
Sampled X:(120, 2) Y:(120, 1) from 663_rabe_266
(120, 2)
(120, 1)


In [2]:
model = run_data_experiment(config)

using backtray...
tensor(4, dtype=torch.int32)
tensor(4, dtype=torch.int32)
AttrDict({'cls': <class 'function_regression.models.urbf_mlp.URBFMLP'>, 'hidden_features': [16, 16, 32, 16, 8], 'use_urbf': True, 'ranges': (0, 100), 'use_split_merge': False, 'split_merge_temperature': 0.1, 'use_back_tray': True, 'back_tray_ratio': 0.5, 'in_features': 2})
fetching: 519_vinnie
Sampled X:(380, 2) Y:(380, 1) from 519_vinnie
Sampled (380, 1)
Updated mean: [  0.        33.333336  66.66667  100.00001    0.         0.
   0.         0.         0.        33.333336  66.66667  100.00001
   0.         0.         0.         0.      ]
Updated vars: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
adding from backtray!
adding from backtray!
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
adding from backtray!
adding from backtray!
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
adding from backtray!
adding 

/Users/dajo/miniconda3/envs/urbf/lib/python3.11/site-packages/exputils/misc/misc.py:592: UserWarning:

Can not find status file location to update its status.



check_for_add_from_back_tray
deactivating... torch.Size([64, 16])
deactivating... torch.Size([12, 16])
Updated mean: [ 0.0000000e+00  3.3333336e+01  6.6666672e+01  1.0000001e+02
  9.9500008e+01  9.9000008e+01  9.8500008e+01  9.8000008e+01
 -1.6669046e-02  3.3333336e+01  6.6666672e+01  1.0000001e+02
  4.9338847e-01 -8.0568772e-03 -1.0906086e-02 -2.2480361e-02]
Updated vars: [1.         1.         1.         1.         1.         1.
 1.         1.         0.98275447 1.         1.         1.
 0.9956868  0.9902366  0.9898911  0.97660893]
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
deactivating... torch.Size([64, 16])
check_for_add_from_back_tray
deactivating... torch.Size([36, 16])
check_for_add_from_back_tray
deactivating... torch.Size([64, 16])
deactivating... torch.Size([12, 16])
Updated mean: [ 0.00000000e+00  3.33333359e+01  6.66666718e+01  1.00000008e+02
  9.95000076e+01  9.90000076e+01  9.8500007

In [3]:
##### keeep in mind! 0-7 input 1
#####                8-15 input 2

import plotly.graph_objects as go
import matplotlib.pyplot as plt
import numpy as np

#print(len(model.layers[0].grads))

steps = []
for i in range(0,len(model.layers[0].grads)):
    grad_step = model.layers[0].grads[i].abs().sum(dim=0).detach().numpy()
    #grad_step = model.layers[0].grads[i].var(dim=0).detach().numpy()
    
    steps.append(grad_step)

data = np.stack(steps,axis=0)

print(data.shape)
# Example data: K vectors with N elements

K = data.shape[0]
N = data.shape[1]

# Creating the plot
fig = go.Figure()

# Adding each of the N lines to the plot
for n in range(N):
    fig.add_trace(go.Scatter(x=list(range(K)), y=data[:, n], mode='lines', name=f'Line {n+1}'))

# Updating the layout of the plot
fig.update_layout(title='Input Grad', xaxis_title='K Steps', yaxis_title='Value')

# Showing the plot
fig.show()



(4000, 16)


In [4]:

import plotly.graph_objects as go
import matplotlib.pyplot as plt
import numpy as np
import torch

data = torch.stack(model.layers[0].acc_grad_hist).detach().numpy()

print(data.shape)


# Example data: K vectors with N elements

K = data.shape[0]
N = data.shape[1]

# Creating the plot
fig = go.Figure()

# Adding each of the N lines to the plot
for n in range(N):
    fig.add_trace(go.Scatter(x=list(range(K)), y=data[:, n], mode='lines', name=f'Line {n+1}'))

# Updating the layout of the plot
fig.update_layout(title='Accumulated Grad', xaxis_title='K Steps', yaxis_title='Value')

# Showing the plot
fig.show()

(4000, 16)


In [5]:

import plotly.graph_objects as go
import matplotlib.pyplot as plt
import numpy as np
import torch

print(len(model.layers[0].means_hist))

data = torch.stack(model.layers[0].means_hist).detach().numpy()

print(data.shape)
# Example data: K vectors with N elements

K = data.shape[0]
N = data.shape[1]

# Creating the plot
fig = go.Figure()

# Adding each of the N lines to the plot
for n in range(N):
    fig.add_trace(go.Scatter(x=list(range(K)), y=data[:, n], mode='lines', name=f'Line {n+1}'))

# Updating the layout of the plot
fig.update_layout(title='N Lines over K Steps', xaxis_title='K Steps', yaxis_title='Value')

# Showing the plot
fig.show()

4000
(4000, 16)


### Observation

When using grad input, the initial grad in the first 20 steps diverges...
- Higher grads indicate higher importance
- Lower grads indicate gaussians with lower importance
  
Note: Neurons at the start might be also low since they might not have a great impact.
There is fluent transition between important and unimportant gaussians... 

This Trend might change later!! 

### Loss

In [6]:

import plotly.graph_objects as go
import matplotlib.pyplot as plt
import numpy as np
import torch

mlp_test_loss = np.load('data_mlp/test_loss.npy')
mlp_train_loss = np.load('data_mlp/train_loss.npy')

mlp_2_test_loss = np.load('data_mlp_2/test_loss.npy')
mlp_2_train_loss = np.load('data_mlp_2/train_loss.npy')

urbf_test_loss = np.load('data_urbf/test_loss.npy')
urbf_train_loss = np.load('data_urbf/train_loss.npy')

sm_test_loss = np.load('data_sm/test_loss.npy')
sm_train_loss = np.load('data_sm/train_loss.npy')

sm_2_test_loss = np.load('data_sm_2/test_loss.npy')
sm_2_train_loss = np.load('data_sm_2/train_loss.npy')

sm_3_test_loss = np.load('data_sm_3/test_loss.npy')
sm_3_train_loss = np.load('data_sm_3/train_loss.npy')


exp_test_loss = np.load('data/test_loss.npy')
exp_train_loss = np.load('data/train_loss.npy')


fig = go.Figure()

K = exp_test_loss.shape[0]

fig.add_trace(go.Scatter(x=list(range(K)), y=mlp_test_loss, mode='lines', name=f'MLP Loss'))
fig.add_trace(go.Scatter(x=list(range(K)), y=mlp_2_test_loss, mode='lines', name=f'MLP 2 Loss'))

fig.add_trace(go.Scatter(x=list(range(K)), y=urbf_test_loss, mode='lines', name=f'URBF Loss'))
fig.add_trace(go.Scatter(x=list(range(K)), y=sm_test_loss, mode='lines', name=f'SM Loss'))
fig.add_trace(go.Scatter(x=list(range(K)), y=sm_2_test_loss, mode='lines', name=f'SM 2 Loss'))
fig.add_trace(go.Scatter(x=list(range(K)), y=sm_3_test_loss, mode='lines', name=f'SM 3 Loss'))


fig.add_trace(go.Scatter(x=list(range(K)), y=exp_test_loss, mode='lines', name=f'Exp Loss'))

# Updating the layout of the plot
fig.update_layout(title='N Lines over K Steps', xaxis_title='K Steps', yaxis_title='Value')

# Showing the plot

fig.show()


Observation:
- Split and Merge outperforms URBF and conventional MLP
- Backtray has no significant benefit
  
- URBF Learning Rate can be chosen higher (x10) than normal learning rate...
- Split Merge Temp < 0.1

In [8]:
from pmlb import fetch_data
from pmlb import classification_dataset_names, regression_dataset_names

print(regression_dataset_names)

for dataset in regression_dataset_names:
    if '712_chscase_geyser1' in dataset:
        print(dataset)


X,Y = fetch_data("712_chscase_geyser1", return_X_y=True,)


print(X.shape)
print(X.min(axis=0))
print(X.max(axis=0))


['1027_ESL', '1028_SWD', '1029_LEV', '1030_ERA', '1089_USCrime', '1096_FacultySalaries', '1191_BNG_pbc', '1193_BNG_lowbwt', '1196_BNG_pharynx', '1199_BNG_echoMonths', '1201_BNG_breastTumor', '1203_BNG_pwLinear', '1595_poker', '192_vineyard', '195_auto_price', '197_cpu_act', '201_pol', '207_autoPrice', '210_cloud', '215_2dplanes', '218_house_8L', '225_puma8NH', '227_cpu_small', '228_elusage', '229_pwLinear', '230_machine_cpu', '294_satellite_image', '344_mv', '4544_GeographicalOriginalofMusic', '485_analcatdata_vehicle', '503_wind', '505_tecator', '519_vinnie', '522_pm10', '523_analcatdata_neavote', '527_analcatdata_election2000', '529_pollen', '537_houses', '542_pollution', '547_no2', '556_analcatdata_apnea2', '557_analcatdata_apnea1', '560_bodyfat', '561_cpu', '562_cpu_small', '564_fried', '573_cpu_act', '574_house_16H', '579_fri_c0_250_5', '581_fri_c3_500_25', '582_fri_c1_500_25', '583_fri_c1_1000_50', '584_fri_c4_500_25', '586_fri_c3_1000_25', '588_fri_c4_1000_100', '589_fri_c2_1000